# Problem Formulation

In this lesson we are going to apply our Feed Forward Neural Network against a real-world classification problem.

First, let's bring back our code for the Feed Forward Network so we can build.

In [4]:
import random
import math

# From First Lesson

class Network:

    def __init__(self, description, initialization_value, learning_rate):
        """
        Initializes the Neural Network
        :param description:  List of how many neurons per layer; size of the list is number of layers
        :param initialization_value: the range from which to initialize the neuron weights
        :param learning_rate: used for training the neural network
        """
        self.Layers = []
        self.Learning_Rate = learning_rate
        # Initialize the input layer
        self.Layers.append(Layer(0, description[0], 0, initialization_value))
        # Initialize the subsequent layers
        for i in range(1, len(description)):
            self.Layers.append(Layer(description[i - 1], description[i], i, initialization_value))

    def set_weights(self, layer_index, neuron_index, weights):
        self.Layers[layer_index].set_weights(neuron_index, weights)


class Layer:

    def __init__(self, number_neurons_previous_layer, number_neurons, layer_index, initialization_value):
        """
        A layer of the network
        :param number_neurons_previous_layer: amount of neurons in the previous layer
        :param number_neurons: amount of neurons in this layer
        :param layer_index: index of this layer (for referencing)
        :param initialization_value: weight initialized between +/- this value
        """
        self.Neurons = []
        self.Layer_Index = layer_index
        for i in range(number_neurons):
            self.Neurons.append(Neuron(number_neurons_previous_layer, i, initialization_value))

    def set_weights(self, neuron_index, weights):
        self.Neurons[neuron_index].set_weights(weights)


class Neuron:

    def __init__(self, number_neurons_in_previous_layer, neuron_index, initialization_value):
        """
        Initializes a neuron in the owning layer
        :param number_neurons_in_previous_layer: number of neurons in previous layer
        :param neuron_index: index of the neuron within the layer
        :param initialization_value: value to initialize this neuron's weights between +/- this value
        """
        self.Weights = []
        self.Result = 0
        self.previous_values = []
        self.delta_weights = []
        self.Neuron_Index = neuron_index
        for i in range(number_neurons_in_previous_layer + 1):
            self.Weights.append(random.uniform(-initialization_value, initialization_value))
        #self.Weights.append(random.uniform(-initialization_value, initialization_value))

    def set_weights(self, weights):
        self.Weights = weights


def print_network(network):
    """
    Prints the current neural network weights and results for each neuron
    """
    print("Neuron_Index: [Weights] => Neuron_Output\n")

    for layer in network.Layers:
        if layer.Layer_Index == 0:
            layer_type = "Input"
        elif layer.Layer_Index == (len(network.Layers) - 1):
            layer_type = "Output"
        else:
            layer_type = "Hidden"
        print("Layer {0} - {1}".format(layer.Layer_Index, layer_type))
        for neuron in layer.Neurons:
            print("   Neuron {0}: {1} => {2}".format(neuron.Neuron_Index, neuron.Weights, neuron.Result))

# Lesson 2


def backward_propagate(network, output_values, correct_values, activation):
    def layer_bp(layer, errors, activation):
        '''
        Takes the errors from the previous layer to update the weights
        :param layer:  the layer being updated
        :param errors:  errors calculated from the previous layer
        :param activation:  the activation function class
        :return:  updated errors for the next layer
        '''
        error_vector = []
        for (neuron, error) in zip(layer.Neurons, errors):
            # calculate each neurons error vector
            error_vector_from_neuron = neuron_back_propagate(neuron,
                                                             error, activation)
            if len(error_vector) == 0:
                for i in range(len(error_vector_from_neuron)):
                    error_vector.append(0)
            for i in range(len(error_vector_from_neuron)):
                error_vector[i] += error_vector_from_neuron[i]
        return error_vector

    def neuron_back_propagate(neuron, error, activation):
        """
        Calculates weight updates for a neuron through back prop
        :param neuron:  the neuron being evaluated
        :param error:  the error associated with this neuron
        :param activation:  the activation function being used
        :return: the error_vector for the
        """
        derivative = activation.activation_function_derivative(neuron.Result)
        error_gradient = error * derivative

        # calculate the change in weights using the error gradient
        neuron.delta_weights.clear()
        for i in range(len(neuron.previous_values)):
            delta = network.Learning_Rate * error_gradient * neuron.previous_values[i]
            neuron.delta_weights.append(delta)
        neuron.delta_weights.append(network.Learning_Rate * error_gradient * -1.0)

        # The error vector becomes the weights modified by the error gradient
        error_vector = []
        for weight in neuron.Weights:
            error_vector.append(weight * error_gradient)
        return error_vector

    errors = []
    # Calculate the error of the prediction at the output layer
    for (output, correct) in zip(output_values, correct_values):
        errors.append(correct - output)

    # move through hidden layers to calculate the error (move from output to input)
    for reversed_layer in reversed(network.Layers[1:]):
        errors = layer_bp(reversed_layer, errors, activation)

    # Update the weights based on the delta calculated
    for layer in network.Layers[1:]:
        for neuron in layer.Neurons:
            for i in range(len(neuron.Weights)):
                neuron.Weights[i] += neuron.delta_weights[i]


def forward_propagate(network, values, activation):
    """
    Runs the forward propagation algorithm
    """
    results = values
    for layer in network.Layers[1:]:
        # initialize a vector for the layer's values (to be sent to next layer)
        values_for_layer = []

        for neuron in layer.Neurons:
            # store the previous values for use in back propagation
            neuron.previous_values = results
            # reset the results
            neuron.Result = 0

            # calculate the weighted sum of the weights by the results
            for i in range(len(results)):
                neuron.Result += neuron.Weights[i] * results[i]
            neuron.Result += -1.0 * neuron.Weights[-1]

            # update the result using the activation function
            neuron.Result = activation.activation_function(neuron.Result)

            # add the new output value to the values vector for the current layer
            values_for_layer.append(neuron.Result)
        results = values_for_layer

    return values_for_layer


class SigmoidActivation:

    @staticmethod
    def activation_function(value):
        return 1 / (1 + math.exp(-value))

    @staticmethod
    def activation_function_derivative(result):
        return result * (1.0 - result)

## Model Training

The above code is a generalizable base code for any classification model.  Thinking about the above model, what set of data elements would you need to fully define a specified network?  

If you answered the weights, then you are correct.  If you think about the above code, all of the training routines are simply there to adjust the weights so that for any standardized input we are able to classify the input vector to some output vector.  Once trained, all of the error correction code is no longer used- it just becomes a forward propagation model.

So then the real magic is in the training routines which generates the weight vector.  Towards this goal, we will need to have three collections of data:
* Training Data - this is the data region we will regularly iterate through forward propagation/back propagation to train the weights.  This should be the only data region which is sent through the training process.
* Validation Data - this data region is used for us to select the optimal weights.  We use this region to prevent the model from overfitting (being useful only on the training data).
* Test Data - This is our confirmation data region.  Data here is withheld and the model is executed against this data set to see that it is able to classify input vectors that were not involved in training or selection

## Sample Problem: XOR
A classic non-linear classification problem is the XOR problem.  The XOR function takes two boolean inputs and returns true only when they are not equal.  In other words XOR(1,0) = 1; XOR(0,1) = 1; XOR(0,0) = 0; and XOR(1,1) = 0.

For our framework we will encapsulate our classification problems as standardized classes.  For these classes we will create four functions:
<code>generate_patterns(amount)</code> - generates amount of patterns within a list

<code>generate_training_set()</code> - generates the training data and solution for the problem

<code>generate_pattern()</code> - generates a single pattern as a vector

<code>generate_solutions(pattern)</code> - given a pattern returns a list of the correct classification

Below is code which implements these methods for the XOR problem

In [5]:
class XORClassificationProblem:
    """
    Classification support methods to support the XOR problem
    """

    def generate_patterns(self, amount):
        """
        Generates a list of data samples
        :param amount: amount of data samples to generate
        :return: list containing tuples of (pattern, solution)
        """
        patterns = []
        for i in range(amount):
            pattern = self.generate_pattern()
            patterns.append((pattern, self.generate_solution(pattern)))
        return patterns

    def generate_training_set(self):
        """
        Generates a set of patterns that encompass the full options
        :return: list of ([pattern], [solution]) tuples
        """
        return[([0, 0], [0]), ([0, 1], [1]), ([1, 0], [1]), ([1, 1], [0])]

    def generate_pattern(self):
        """
        Generates a single pattern for this problem
        :return: a list containing a single input for the problem
        """
        return [random.randint(0, 1), random.randint(0, 1)]

    def generate_solution(self, pattern):
        """
        Given the pattern generates the true solution
        :param pattern: input pattern as a list
        :return: the list containing the true results from the pattern
        """
        return [pattern[0] ^ pattern[1]]


The next item we need to look at is to build an objective function so that we are able to update the weights towards a goal.  For these types of algorithms you will commonly see a term known as the Sum Squared Error, or SSE.  SSE is the sum of the difference from what is expected against what is generated for all of the patterns in a data region.  See below for a function which calculates the SSE.

In [6]:
def calculate_SSE(network, activation, test_data):
    """
    Iterates through the test data on the given network to calculate the current SSE
    :param network: the neural network being examined
    :param activation: the activation function used for the neural net
    :param test_data: test data iterated over for the solution
    :return: the calculated SSE
    """
    total_error = 0
    for element in test_data:
        result = forward_propagate(network, element[0], activation)
        for (output, actual) in zip(result, element[1]):
            total_error = total_error + (output - actual)**2
    return total_error

Now it is time to train!  For training we are going to iterate through our training data several times.  Each time we iterate over all of the elements in the training data is called an epoch.  We will want to run our training routine against the training data for several (sometimes thousands) of epochs to minimize the SSE of our validatation data.

In [7]:
def train_neural_network(network, training_data, validation_data, acceptable_SSE, activation):
    """
    Runs the neural network through several training epochs
    :param network: the neural network being trained
    :param training_data: a list of training data to be iterated over
    :param validation_data: a list of validation data
    :param acceptable_SSE: the desired sum squared error for convergence
    :param activation: the class containing the selected activation function
    :param test_type: the
    :return:
    """
    error = 100
    epoch_counter = 0
    while error > acceptable_SSE or epoch_counter < 10000:
        # train
        for element in training_data:
            result = forward_propagate(network, element[0], activation)
            backward_propagate(network, result, element[1], activation)

        error = calculate_SSE(network, activation, validation_data)
        print("Finished epoch {0} with SSE {1}".format(epoch_counter, error))
        epoch_counter += 1
    print("Training completed in {0} epochs with an error of {1}".format(epoch_counter, error))

It is now time to put it all together and run our model!



In [9]:
# Create our neural network structure
init_value = 2.4/2  # per Haykin set the init to 2.4/<number input neurons>
network = Network([2, 2, 1], init_value, 0.1)
activation = SigmoidActivation()

# Create the XOR problem
XOR_problem = XORClassificationProblem()

# Generate the training data
train = XOR_problem.generate_training_set()

# Generate the validation and test data
val = XOR_problem.generate_patterns(100)  # 100 validation examples
test = XOR_problem.generate_patterns(100)

# Train the network to an SSE of 0.001
train_neural_network(network, train, val, 0.01, activation)

Finished epoch 0 with SSE 30.479069155901975
Finished epoch 1 with SSE 30.180425387851077
Finished epoch 2 with SSE 29.89089959952714
Finished epoch 3 with SSE 29.610947386963247
Finished epoch 4 with SSE 29.340947551090572
Finished epoch 5 with SSE 29.08120061173242
Finished epoch 6 with SSE 28.831928844962377
Finished epoch 7 with SSE 28.593277753595306
Finished epoch 8 with SSE 28.365318835794234
Finished epoch 9 with SSE 28.148053481962826
Finished epoch 10 with SSE 27.94141780626857
Finished epoch 11 with SSE 27.745288206442464
Finished epoch 12 with SSE 27.559487443279647
Finished epoch 13 with SSE 27.38379103826965
Finished epoch 14 with SSE 27.217933802340717
Finished epoch 15 with SSE 27.061616328901582
Finished epoch 16 with SSE 26.914511308293445
Finished epoch 17 with SSE 26.776269546592342
Finished epoch 18 with SSE 26.646525597843716
Finished epoch 19 with SSE 26.524902943964943
Finished epoch 20 with SSE 26.411018679732916
Finished epoch 21 with SSE 26.304487680822096
Fi

Finished epoch 220 with SSE 24.822185880683996
Finished epoch 221 with SSE 24.822125261057757
Finished epoch 222 with SSE 24.82206461148801
Finished epoch 223 with SSE 24.822003925804214
Finished epoch 224 with SSE 24.821943198051674
Finished epoch 225 with SSE 24.821882422481966
Finished epoch 226 with SSE 24.821821593544055
Finished epoch 227 with SSE 24.821760705875132
Finished epoch 228 with SSE 24.821699754292464
Finished epoch 229 with SSE 24.821638733785253
Finished epoch 230 with SSE 24.821577639507183
Finished epoch 231 with SSE 24.821516466769026
Finished epoch 232 with SSE 24.821455211031722
Finished epoch 233 with SSE 24.82139386789957
Finished epoch 234 with SSE 24.821332433114215
Finished epoch 235 with SSE 24.82127090254837
Finished epoch 236 with SSE 24.821209272200083
Finished epoch 237 with SSE 24.821147538187255
Finished epoch 238 with SSE 24.821085696742298
Finished epoch 239 with SSE 24.82102374420725
Finished epoch 240 with SSE 24.820961677028755
Finished epoch 24

Finished epoch 443 with SSE 24.80345184615243
Finished epoch 444 with SSE 24.803332812669435
Finished epoch 445 with SSE 24.803213386585135
Finished epoch 446 with SSE 24.80309356693193
Finished epoch 447 with SSE 24.8029733527427
Finished epoch 448 with SSE 24.802852743050842
Finished epoch 449 with SSE 24.802731736890326
Finished epoch 450 with SSE 24.8026103332956
Finished epoch 451 with SSE 24.80248853130163
Finished epoch 452 with SSE 24.802366329943883
Finished epoch 453 with SSE 24.802243728258286
Finished epoch 454 with SSE 24.802120725281238
Finished epoch 455 with SSE 24.801997320049487
Finished epoch 456 with SSE 24.801873511600284
Finished epoch 457 with SSE 24.801749298971355
Finished epoch 458 with SSE 24.80162468120068
Finished epoch 459 with SSE 24.80149965732674
Finished epoch 460 with SSE 24.801374226388372
Finished epoch 461 with SSE 24.80124838742471
Finished epoch 462 with SSE 24.801122139475197
Finished epoch 463 with SSE 24.800995481579804
Finished epoch 464 with

Finished epoch 643 with SSE 24.770563025957458
Finished epoch 644 with SSE 24.770346077143664
Finished epoch 645 with SSE 24.770128535849523
Finished epoch 646 with SSE 24.769910400959724
Finished epoch 647 with SSE 24.769691671356792
Finished epoch 648 with SSE 24.769472345921383
Finished epoch 649 with SSE 24.76925242353204
Finished epoch 650 with SSE 24.769031903065446
Finished epoch 651 with SSE 24.768810783396194
Finished epoch 652 with SSE 24.768589063396732
Finished epoch 653 with SSE 24.76836674193765
Finished epoch 654 with SSE 24.768143817887278
Finished epoch 655 with SSE 24.767920290112112
Finished epoch 656 with SSE 24.767696157476287
Finished epoch 657 with SSE 24.76747141884209
Finished epoch 658 with SSE 24.76724607306949
Finished epoch 659 with SSE 24.76702011901652
Finished epoch 660 with SSE 24.76679355553892
Finished epoch 661 with SSE 24.766566381490435
Finished epoch 662 with SSE 24.76633859572244
Finished epoch 663 with SSE 24.76611019708443
Finished epoch 664 wi

Finished epoch 839 with SSE 24.715194035285265
Finished epoch 840 with SSE 24.71483645603
Finished epoch 841 with SSE 24.714478012271776
Finished epoch 842 with SSE 24.71411870226112
Finished epoch 843 with SSE 24.713758524244373
Finished epoch 844 with SSE 24.71339747646289
Finished epoch 845 with SSE 24.713035557153596
Finished epoch 846 with SSE 24.712672764548653
Finished epoch 847 with SSE 24.712309096875607
Finished epoch 848 with SSE 24.711944552357284
Finished epoch 849 with SSE 24.711579129211742
Finished epoch 850 with SSE 24.711212825652343
Finished epoch 851 with SSE 24.71084563988786
Finished epoch 852 with SSE 24.710477570122045
Finished epoch 853 with SSE 24.710108614554056
Finished epoch 854 with SSE 24.709738771378213
Finished epoch 855 with SSE 24.709368038783985
Finished epoch 856 with SSE 24.708996414956122
Finished epoch 857 with SSE 24.70862389807438
Finished epoch 858 with SSE 24.708250486313947
Finished epoch 859 with SSE 24.707876177844696
Finished epoch 860 wi

...

Finished epoch 131719 with SSE 0.010103477628811225
Finished epoch 131720 with SSE 0.010103395114202466
Finished epoch 131721 with SSE 0.010103312600922404
Finished epoch 131722 with SSE 0.010103230088970728
Finished epoch 131723 with SSE 0.010103147578347491
Finished epoch 131724 with SSE 0.010103065069052713
Finished epoch 131725 with SSE 0.010102982561086184
Finished epoch 131726 with SSE 0.010102900054448131
Finished epoch 131727 with SSE 0.010102817549138268
Finished epoch 131728 with SSE 0.010102735045156703
Finished epoch 131729 with SSE 0.010102652542503485
Finished epoch 131730 with SSE 0.010102570041178304
Finished epoch 131731 with SSE 0.01010248754118153
Finished epoch 131732 with SSE 0.010102405042512653
Finished epoch 131733 with SSE 0.010102322545172071
Finished epoch 131734 with SSE 0.010102240049159534
Finished epoch 131735 with SSE 0.010102157554474932
Finished epoch 131736 with SSE 0.010102075061118652
Finished epoch 131737 with SSE 0.010101992569089956
Finished epoc

Finished epoch 131970 with SSE 0.010082808060844618
Finished epoch 131971 with SSE 0.010082725878691799
Finished epoch 131972 with SSE 0.010082643697859337
Finished epoch 131973 with SSE 0.01008256151834759
Finished epoch 131974 with SSE 0.010082479340156254
Finished epoch 131975 with SSE 0.010082397163285338
Finished epoch 131976 with SSE 0.010082314987734785
Finished epoch 131977 with SSE 0.010082232813504613
Finished epoch 131978 with SSE 0.010082150640594765
Finished epoch 131979 with SSE 0.010082068469005286
Finished epoch 131980 with SSE 0.01008198629873612
Finished epoch 131981 with SSE 0.01008190412978702
Finished epoch 131982 with SSE 0.010081821962158422
Finished epoch 131983 with SSE 0.010081739795849703
Finished epoch 131984 with SSE 0.010081657630861371
Finished epoch 131985 with SSE 0.010081575467192998
Finished epoch 131986 with SSE 0.010081493304844856
Finished epoch 131987 with SSE 0.010081411143816643
Finished epoch 131988 with SSE 0.010081328984108497
Finished epoch 

Finished epoch 132231 with SSE 0.01006140323213413
Finished epoch 132232 with SSE 0.010061321393570013
Finished epoch 132233 with SSE 0.010061239556318177
Finished epoch 132234 with SSE 0.010061157720378753
Finished epoch 132235 with SSE 0.010061075885751444
Finished epoch 132236 with SSE 0.010060994052436486
Finished epoch 132237 with SSE 0.010060912220433538
Finished epoch 132238 with SSE 0.010060830389742896
Finished epoch 132239 with SSE 0.010060748560364213
Finished epoch 132240 with SSE 0.01006066673229778
Finished epoch 132241 with SSE 0.010060584905543409
Finished epoch 132242 with SSE 0.010060503080100999
Finished epoch 132243 with SSE 0.010060421255970614
Finished epoch 132244 with SSE 0.010060339433152102
Finished epoch 132245 with SSE 0.01006025761164562
Finished epoch 132246 with SSE 0.01006017579145102
Finished epoch 132247 with SSE 0.01006009397256846
Finished epoch 132248 with SSE 0.010060012154997564
Finished epoch 132249 with SSE 0.010059930338738393
Finished epoch 13

Finished epoch 132497 with SSE 0.010039680329511115
Finished epoch 132498 with SSE 0.01003959883892021
Finished epoch 132499 with SSE 0.010039517349633377
Finished epoch 132500 with SSE 0.01003943586165049
Finished epoch 132501 with SSE 0.010039354374971585
Finished epoch 132502 with SSE 0.010039272889596662
Finished epoch 132503 with SSE 0.010039191405525533
Finished epoch 132504 with SSE 0.010039109922758357
Finished epoch 132505 with SSE 0.010039028441294836
Finished epoch 132506 with SSE 0.010038946961135244
Finished epoch 132507 with SSE 0.010038865482279396
Finished epoch 132508 with SSE 0.010038784004727222
Finished epoch 132509 with SSE 0.010038702528478745
Finished epoch 132510 with SSE 0.010038621053533984
Finished epoch 132511 with SSE 0.010038539579892803
Finished epoch 132512 with SSE 0.010038458107555244
Finished epoch 132513 with SSE 0.010038376636521195
Finished epoch 132514 with SSE 0.010038295166790896
Finished epoch 132515 with SSE 0.01003821369836398
Finished epoch 

Finished epoch 132816 with SSE 0.010013750805398493
Finished epoch 132817 with SSE 0.010013669729214567
Finished epoch 132818 with SSE 0.010013588654324534
Finished epoch 132819 with SSE 0.01001350758072884
Finished epoch 132820 with SSE 0.010013426508427051
Finished epoch 132821 with SSE 0.010013345437419245
Finished epoch 132822 with SSE 0.010013264367705697
Finished epoch 132823 with SSE 0.010013183299285912
Finished epoch 132824 with SSE 0.010013102232160235
Finished epoch 132825 with SSE 0.010013021166328517
Finished epoch 132826 with SSE 0.010012940101790577
Finished epoch 132827 with SSE 0.010012859038546481
Finished epoch 132828 with SSE 0.01001277797659628
Finished epoch 132829 with SSE 0.010012696915939845
Finished epoch 132830 with SSE 0.010012615856577308
Finished epoch 132831 with SSE 0.010012534798508377
Finished epoch 132832 with SSE 0.010012453741733117
Finished epoch 132833 with SSE 0.010012372686251686
Finished epoch 132834 with SSE 0.010012291632063798
Finished epoch

In [10]:
# Calculate the overall error of our holdout data (Test)
error = calculate_SSE(network, activation, test)
print("Model resulted in a SSE of {0} on the holdout (test) data".format(error))

Model resulted in a SSE of 0.00999117370634573 on the holdout (test) data


While the SSE is a useful metric, remember the main point is the classification to return either 1 or 0 based on the input vector.  Perhaps a better measure for this specific problem is instead a count of the actual classification from the resulting output vector.  Let's see how well we did our classification with the below:

In [18]:
def calculate_classification_error_count(network, activation, test_data):
    """
    Iterates through the test data on the given network to calculate the number correctly classified
    :param network: the neural network being examined
    :param activation: the activation function used for the neural net
    :param test_data: test data iterated over for the solution
    :return: the amount of items correctly classified
    """
    count_correct = 0
    for element in test_data:
        is_correct = True
        result = forward_propagate(network, element[0], activation)
        for (output, actual) in zip(result, element[1]):
            if round(output) != actual:
                is_correct = False
        if is_correct:
            count_correct = count_correct + 1
    return count_correct

number_correct = calculate_classification_error_count(network, activation, test)
print("Model resulted in classifying {0} of {1} items from the test data".format(number_correct,len(test)))

Model resulted in classifying 100 of 100 items from the test data


Congratulations, you have a fully functional neural network.  Now you get to try to build and test your own.  In the below code blocks implement code to run a classification algorithm to classify the AND problem (AND(1,1)=1 else 0)